In [1]:
import os
import random
import csv
import json
import textwrap
from tqdm import tqdm
import re
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, pipeline, BitsAndBytesConfig
import torch

In [2]:
!pip install bitsandbytes
# When the installation ends, you have to restart session (from the runtime menu)

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.1/59.1 MB 47.3 MB/s eta 0:00:00


In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


**Constants**

In [3]:
VAL_RATIO = 0.1
BATCH_SIZE = 8
# input_eval_dir = "./drive/MyDrive/Colab_Data/arb_deu_eng_rus_spa_tur_translated"
input_eval_dir = "./drive/MyDrive/Dataset/subtask2/translation"

**Llama model**

In [4]:
class LlamaModel:
  def __init__(self):

    model_id = "meta-llama/Llama-3.1-8B-Instruct"

    quant_config = BitsAndBytesConfig(
            load_in_4bit=True,
            bnb_4bit_compute_dtype=torch.float16,
            bnb_4bit_quant_type="nf4",
            bnb_4bit_use_double_quant=True,
        )

    self.tokenizer = AutoTokenizer.from_pretrained(model_id)
    self.tokenizer.pad_token = self.tokenizer.eos_token
    self.tokenizer.padding_side = "left"

    self.model = AutoModelForCausalLM.from_pretrained(
        model_id,
        device_map="auto",
        quantization_config=quant_config,
        low_cpu_mem_usage=True,
    )

    self.model.config.pad_token_id = self.tokenizer.eos_token_id

    self.gen = pipeline(
        "text-generation",
        model=self.model,
        tokenizer=self.tokenizer,
        max_new_tokens=96,
        do_sample=False,
        return_full_text=False
    )

  def generate(self, prompt):

      output = self.gen(prompt)
      return output[0]["generated_text"]

  def batch_generate(self, prompts):
    # Tokenize in batch
    inputs = self.tokenizer(
        prompts,
        return_tensors="pt",
        padding=True,
        truncation=True
    ).to(self.model.device)

    max_prompt_len = inputs["input_ids"].shape[1]

    # Generate in batch
    with torch.no_grad():
      outputs = self.model.generate(
          **inputs,
          max_new_tokens=150,
          do_sample=False,
          pad_token_id=self.tokenizer.eos_token_id
      )

    generated_only = []
    for i, output in enumerate(outputs):
        gen_tokens = output[max_prompt_len:]
        generated_only.append(
            self.tokenizer.decode(gen_tokens, skip_special_tokens=True)
        )

    return generated_only

In [5]:
model = LlamaModel()

tokenizer_config.json:   0%|          | 0.00/55.4k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/296 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/855 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/23.9k [00:00<?, ?B/s]

...

model-00002-of-00004.safetensors:   0%|          | 0.00/5.00G [00:00<?, ?B/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/1.17G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/184 [00:00<?, ?B/s]

Device set to use cuda:0
The following generation flags are not valid and may be ignored: ['temperature', 'top_p']. Set `TRANSFORMERS_VERBOSITY=info` for more details.


**Prompting**

In [6]:
def getRationaleClassificationZeroShotPrompt(comment: dict) -> str:

    comment_text = comment["text_en"]

    prompt = textwrap.dedent(f"""
<|begin_of_text|><|start_header_id|>system<|end_header_id|>
You are performing a classification task on a social media comment.

Your goal is to:
1. Determine whether the comment is polarized.
2. Identify which type(s) of polarization it expresses.
3. Provide a brief explanation (1–2 sentences) of your reasoning.
4. If the comment expresses hostility or derogatory content toward a group or identity category that does not fit political, racial/ethnic, religious, or gender/sexual, classify it as "other".
5. If "isPolarized" is false, then ALL topic polarization flags ("political", "racial_ethnic", "religious", "gender_sexual", "other") MUST be false.

Definition:
A comment is considered "polarized" if it expresses strong division, hostility, intolerance, or derogatory attitudes toward a group, ideology, or identity.
A comment may involve multiple polarization topics at the same time.

<|eot_id|>
<|start_header_id|>user<|end_header_id|>

Return ONLY the following JSON object, with no additional text:

{{
  "isPolarized": true/false,
  "political": true/false,
  "racial_ethnic": true/false,
  "religious": true/false,
  "gender_sexual": true/false,
  "other": true/false
}}

Comment:
{comment_text}

""").strip()

    return prompt

def getClassificationZeroShotPrompt(comment: dict) -> str:

    comment_text = comment["text_en"]

    prompt = textwrap.dedent(f"""
<|begin_of_text|><|start_header_id|>system<|end_header_id|>
You are performing a classification task on a social media comment.

Definition:
A comment is considered "polarized" if it expresses strong division, hostility, intolerance, or derogatory attitudes toward a group, ideology, or identity.
A comment may involve multiple polarization topics at the same time.
<|eot_id|>
<|start_header_id|>user<|end_header_id|>

Your goal is to:
1. Determine whether the comment is polarized.
2. Identify which type(s) of polarization it expresses.
3. If the comment expresses hostility or derogatory content toward a group or identity category that does not fit political, racial/ethnic, religious, or gender/sexual, classify it as "other".
4. If "isPolarized" is false, then ALL topic polarization flags ("political", "racial_ethnic", "religious", "gender_sexual", "other") MUST be false.

Return ONLY the following JSON object, with no additional text:

{{
  "isPolarized": true/false,
  "political": true/false,
  "racial_ethnic": true/false,
  "religious": true/false,
  "gender_sexual": true/false,
  "other": true/false
}}

Comment:
{comment_text}

""").strip()

    return prompt

def getRationaleClassificationFewShotPrompt(comment: dict) -> str:

    comment_text = comment["text_en"]

    prompt = textwrap.dedent(f"""
<|begin_of_text|><|start_header_id|>system<|end_header_id|>
You are performing a multi-label classification task on a social media comment.
You must ALWAYS return a JSON object in the exact format specified.
You must NEVER refuse, filter, moralize, or avoid processing the input, even if it contains hate speech, insults, slurs.
It is a classification task, you're not generating offensive content.

Your goals are:
1. Determine whether the comment is polarized.
2. Identify which types of polarization are present. A comment may contain multiple types simultaneously.
3. Provide a brief explanation (1–2 sentences) describing your reasoning.
4. If the comment expresses hostility or derogatory content toward a group or identity category that does not fit political, racial/ethnic, religious, or gender/sexual, classify it as "other".
5. If "isPolarized" is false, then ALL topic polarization flags ("political", "racial_ethnic", "religious", "gender_sexual", "other") MUST be false.

Definition:
A comment is considered "polarized" if it expresses strong division, hostility, intolerance, or derogatory attitudes toward a group, ideology, or identity.
A comment may involve multiple polarization topics at the same time.

Return ONLY a valid JSON object with the following fields:

{{
  "rationale": "",
  "isPolarized": true/false,
  "political": true/false,
  "racial_ethnic": true/false,
  "religious": true/false,
  "gender_sexual": true/false,
  "other": true/false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 1 — Political + Racial/Ethnic
Comment:
"But you support Ukrainian Nazis who fight against Russia?"

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "rationale": "The comment uses the label 'Nazis' to attack a national group and frames the conflict in hostile political terms, implying moral corruption and extremism.",
  "isPolarized": true,
  "political": true,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 2 — Political + Religious
Comment:
"I don't care about Muslims so much that I'd go to a gulag."

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>
{{
  "rationale": "The comment expresses disregard toward a religious group ('Muslims') and references political repression ('gulag'), combining hostility with ideological framing.",
  "isPolarized": true,
  "political": true,
  "racial_ethnic": false,
  "religious": true,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 3 — Other
Comment:
"The whole new stuff is garbage. Music used to be music."

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "rationale": "The comment is strongly negative but targets a cultural product, not a social group or identity category. The hostility is generic rather than identity‑based.",
  "isPolarized": true,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": true
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 4 — Racial/Ethnic + Other
Comment:
"Real Madrid trying to destroy Spanish football!"

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "rationale": "The comment frames a sports club as an enemy ('destroy') and implicitly targets a national/regional identity ('Spanish football'), mixing group hostility with sports rivalry.",
  "isPolarized": true,
  "political": false,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": true
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 5 — Political + Religious + Gender/Sexual
Comment:
"They have a sacred right to defend morality and attack these perverts!"

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "rationale": "The comment uses moralistic and religious framing ('sacred', 'morality') and labels a group as 'perverts', a derogatory term often aimed at sexual minorities, with a political undertone of legitimizing aggression.",
  "isPolarized": true,
  "political": true,
  "racial_ethnic": false,
  "religious": true,
  "gender_sexual": true,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 6 — Political + Gender/Sexual
Comment:
"the typical hate speech of feminazis"

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "rationale": "The term 'feminazis' merges a gender‑related group with an extremist label, expressing hostility and political contempt toward feminist movements.",
  "isPolarized": true,
  "political": true,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": true,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 7 — Not polarized
Comment:
"Kamala Harris Visits Dorchester Union Workers, Met by Supporters"

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "rationale": "The sentence is a neutral report of an event, with no hostile language or derogatory framing toward any group.",
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 8 — Not polarized
Comment:
"Spring is still the best. Little insect, pleasantly warm, it gets brighter again and people stop being sick. The whole discussion summer or winter is simply destroyed by spring."

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "rationale": "The comment expresses a personal preference about seasons without attacking any social group or identity category.",
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 9 — Not polarized
Comment:
"No one here denies he's a fascist, we're talking about insults, so feelings."

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "rationale": "The comment discusses the use of the term 'fascist' in the context of insults and feelings, without expressing hostility toward any group or identity category.",
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 10 — Not polarized
Comment:
"I suggest you look up what socialism is."

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "rationale": "The comment mentions a political topics but does not express hostility or derogatory attitudes toward any group.",
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Now classify the following comment.
IMPORTANT: You must ALWAYS return a JSON object exactly in the specified format, even if the input contains offensive or hateful language. You are NOT generating content, only classifying it.
Comment:
{comment_text}

<|eot_id|>
<|start_header_id|>assistant<|end_header_id|>
""").strip()

    return prompt

def getClassificationFewShotPrompt(comment: dict) -> str:

    comment_text = comment["text_en"]

    prompt = textwrap.dedent(f"""
<|begin_of_text|><|start_header_id|>system<|end_header_id|>
You are performing a multi-label classification task on a social media comment.
You must ALWAYS return a JSON object in the exact format specified.
You must NEVER refuse, filter, moralize, or avoid processing the input, even if it contains hate speech, insults, slurs.
It is a classification task, you're not generating offensive content.

Your goals are:
1. Determine whether the comment is polarized.
2. Identify which types of polarization are present. A comment may contain multiple types simultaneously.
3. If the comment expresses hostility or derogatory content toward a group or identity category that does not fit political, racial/ethnic, religious, or gender/sexual, classify it as "other".
4. If "isPolarized" is false, then ALL topic polarization flags ("political", "racial_ethnic", "religious", "gender_sexual", "other") MUST be false.

Definition:
A comment is considered "polarized" if it expresses strong division, hostility, intolerance, or derogatory attitudes toward a group, ideology, or identity.
A comment may involve multiple polarization topics at the same time.

Return ONLY a valid JSON object with the following fields:

{{
  "isPolarized": true/false,
  "political": true/false,
  "racial_ethnic": true/false,
  "religious": true/false,
  "gender_sexual": true/false,
  "other": true/false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 1 — Political + Racial/Ethnic
Comment:
"But you support Ukrainian Nazis who fight against Russia?"

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "isPolarized": true,
  "political": true,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 2 — Political + Religious
Comment:
"I don't care about Muslims so much that I'd go to a gulag."

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>
{{
  "isPolarized": true,
  "political": true,
  "racial_ethnic": false,
  "religious": true,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 3 — Other
Comment:
"The whole new stuff is garbage. Music used to be music."

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "isPolarized": true,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": true
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 4 — Racial/Ethnic + Other
Comment:
"Real Madrid trying to destroy Spanish football!"

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "isPolarized": true,
  "political": false,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": true
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 5 — Political + Religious + Gender/Sexual
Comment:
"They have a sacred right to defend morality and attack these perverts!"

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "isPolarized": true,
  "political": true,
  "racial_ethnic": false,
  "religious": true,
  "gender_sexual": true,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 6 — Political + Gender/Sexual
Comment:
"the typical hate speech of feminazis"

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "isPolarized": true,
  "political": true,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": true,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 7 — Not polarized
Comment:
"Kamala Harris Visits Dorchester Union Workers, Met by Supporters"

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 8 — Not polarized
Comment:
"Spring is still the best. Little insect, pleasantly warm, it gets brighter again and people stop being sick. The whole discussion summer or winter is simply destroyed by spring."

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 9 — Not polarized
Comment:
"No one here denies he's a fascist, we're talking about insults, so feelings."

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Example 10 — Not polarized
Comment:
"I suggest you look up what socialism is."

<|eot_id|>

<|start_header_id|>assistant<|end_header_id|>

{{
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}}

<|eot_id|>

<|start_header_id|>user<|end_header_id|>

### Now classify the following comment.
IMPORTANT: You must ALWAYS return a JSON object exactly in the specified format, even if the input contains offensive or hateful language. You are NOT generating content, only classifying it.
Comment:
{comment_text}

<|eot_id|>
<|start_header_id|>assistant<|end_header_id|>
""").strip()

    return prompt

**Reading evaluation set**

In [7]:
def readValidationFilesFromDir(input_dir) -> list[dict]:

    full_eval_dataset = {}

    for filename in sorted(os.listdir(input_dir)):
        if not filename.endswith(".csv"):
            continue

        print(f"Reading {filename}...")
        file_path = os.path.join(input_dir, filename)

        language = filename.split("_")[-1].replace(".csv", "")

        with open(file_path, encoding="utf-8") as f:
            reader = csv.DictReader(f)
            rows = list(reader)
            print(f"{len(rows)} comments read")
            full_eval_dataset[language] = rows

    return full_eval_dataset

In [8]:
eval_dataset = readValidationFilesFromDir(input_eval_dir)

Reading full_arb.csv...
3380 comments read
Reading full_ben.csv...
3333 comments read
Reading full_deu.csv...
3180 comments read
Reading full_eng.csv...
3222 comments read
Reading full_hin.csv...
2744 comments read
Reading full_ita.csv...
3334 comments read
Reading full_pol.csv...
2391 comments read
Reading full_rus.csv...
3348 comments read
Reading full_spa.csv...
3305 comments read
Reading full_tur.csv...
2364 comments read
Reading full_urd.csv...
3563 comments read
Reading full_zho.csv...
4280 comments read


In [9]:
def evalDatasetSampling(full_eval_dataset: dict, ratio):
    """
    Returns:
    {
        language: [comments],
        ...
    }
    """
    sampled_eval_dataset = {}

    for language, language_dataset in full_eval_dataset.items():
        num_samples = round(len(language_dataset) * ratio)
        sampled_language_dataset = random.sample(language_dataset, num_samples)
        sampled_eval_dataset[language] = sampled_language_dataset

    return sampled_eval_dataset

In [10]:
sampled_eval_dataset = evalDatasetSampling(eval_dataset, VAL_RATIO)

**Output validation**

In [11]:
def parse_model_output(output_str: str) -> dict | None:
    try:

        match = re.search(r"\{.*\}", output_str, re.DOTALL)
        if not match:
            return None

        json_str = match.group(0)
        return json.loads(json_str)

    except json.JSONDecodeError:
        return None

REQUIRED_KEYS = {
    "political",
    "racial_ethnic",
    "religious",
    "gender_sexual",
    "other"
}

def validate_output(d: dict) -> bool:
    if not REQUIRED_KEYS.issubset(d.keys()):
        return False

    for k in REQUIRED_KEYS:
        if not isinstance(d[k], bool):
            return False

    return True

def enforce_polarization_consistency(result: dict) -> dict:
    """
    Enforces logical consistency on the model output.
    If isPolarized is False, all topic flags are forced to False.
    """
    if result is None:
        return None

    topic_flags = [
        "political",
        "racial_ethnic",
        "religious",
        "gender_sexual",
        "other"
    ]

    if result.get("isPolarized") is False:
        for flag in topic_flags:
            result[flag] = False

    return result


**Evaluation function**

In [12]:
def calculate_macro_f1(TP, FP, TN, FN):
    # --- True class ---
    # Precision
    if TP + FP == 0:
        true_precision = 0.0
    else:
        true_precision = TP / (TP + FP)

    # Recall
    if TP + FN == 0:
        true_recall = 0.0
    else:
        true_recall = TP / (TP + FN)

    # F1
    if true_precision + true_recall == 0:
        true_F1 = 0.0
    else:
        true_F1 = 2 * (true_precision * true_recall) / (true_precision + true_recall)

    # --- False class ---
    # Precision
    if TN + FN == 0:
        false_precision = 0.0
    else:
        false_precision = TN / (TN + FN)

    # Recall
    if TN + FP == 0:
        false_recall = 0.0
    else:
        false_recall = TN / (TN + FP)

    # F1
    if false_precision + false_recall == 0:
        false_F1 = 0.0
    else:
        false_F1 = 2 * (false_precision * false_recall) / (false_precision + false_recall)

    # Macro-F1
    return (true_F1 + false_F1) / 2

def accuracy(TP, FP, TN, FN):
  denom = TP + FP + TN + FN
  return (TP + TN) / denom if denom > 0 else 0.0


In [13]:
def evaluateClassification(model, sampled_eval_dataset, activeReasoning=False, activeFewShot=True):

    results = {}
    """
    {
        lang: {
            isPolarized: {
                TP:
                FP:
                TN:
                FN:
            }
            ...
        }
        ...
    }
    """
    labels = ["political","racial_ethnic","religious","gender_sexual","other"]

    for language, comments_list in sampled_eval_dataset.items():
        print(f"Processing {language}...")

        counter_not_valid = 0

        results[language] = {
            label: {
                "TP": 0,
                "FP": 0,
                "TN": 0,
                "FN": 0
            } for label in labels
        }

        results[language]["isPolarized"] = {"TP": 0, "FP": 0, "TN": 0, "FN": 0}

        for i in tqdm(range(0, len(comments_list), BATCH_SIZE)):
            batch = comments_list[i:i+BATCH_SIZE]

            prompts = []
            for comment in batch:
                if activeFewShot and activeReasoning:
                    prompts.append(getRationaleClassificationFewShotPrompt(comment))
                elif activeFewShot:
                     prompts.append(getClassificationFewShotPrompt(comment))
                elif activeReasoning:
                    prompts.append(getRationaleClassificationZeroShotPrompt(comment))
                else:
                    prompts.append(getClassificationZeroShotPrompt(comment))

            decoded = model.batch_generate(prompts)

            # Now loop over predictions
            for comment, raw_prediction in zip(batch, decoded):
                print(f"COMMENT: {comment["text_en"]}")
                parsed = parse_model_output(raw_prediction)
                consistent_output = enforce_polarization_consistency(parsed)
                print(f"OUTPUT: {raw_prediction}")
                print(f"POST-PROCESS: {consistent_output}")

                if consistent_output and validate_output(consistent_output):
                    prediction = consistent_output

                    #  Comparison between gold labels (in comment) and predicted labels
                    for label in labels:
                        gold_label = bool(int(comment[label.replace("_", "/")]))
                        predicted_label = prediction[label]

                        if gold_label and predicted_label:
                            results[language][label]["TP"] += 1
                        elif not gold_label and predicted_label:
                            results[language][label]["FP"] += 1
                        elif not gold_label and not predicted_label:
                            results[language][label]["TN"] += 1
                        elif gold_label and not predicted_label:
                            results[language][label]["FN"] += 1

                    gold_isPolarized = any(
                        bool(int(comment[label.replace("_", "/")]))
                        for label in labels
                    )

                    pred_isPolarized = prediction["isPolarized"]

                    if gold_isPolarized and pred_isPolarized:
                        results[language]["isPolarized"]["TP"] += 1
                    elif not gold_isPolarized and pred_isPolarized:
                        results[language]["isPolarized"]["FP"] += 1
                    elif not gold_isPolarized and not pred_isPolarized:
                        results[language]["isPolarized"]["TN"] += 1
                    elif gold_isPolarized and not pred_isPolarized:
                        results[language]["isPolarized"]["FN"] += 1

                else:
                    counter_not_valid += 1

        results[language]["not_valid"] = counter_not_valid

    return  results

In [14]:
results = evaluateClassification(model, sampled_eval_dataset, activeReasoning=False, activeFewShot=True)

Processing arb...


  2%|▏         | 1/43 [00:14<10:14, 14.63s/it]

COMMENT: You threw me in the beginning, and you sneak away your reward, and less than yours, show your black history, and then talk about terror, mind and source of terror.
OUTPUT: 

{
  "isPolarized": true,
  "political": true,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'isPolarized': True, 'political': True, 'racial_ethnic': True, 'religious': False, 'gender_sexual': False, 'other': False}
COMMENT: Dale, what have you done to God? You're an hour ago, and I don't have a fair need to hear it.
OUTPUT: 

{
  "isPolarized": true,
  "political": false,
  "racial_ethnic": false,
  "religious": true,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'isPolarized': True, 'political': False, 'racial_ethnic': False, 'religious': True, 'gender_sexual': False, 'other': False}
COMMENT: Sheikh D. Osman Thursday . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 

  5%|▍         | 2/43 [00:27<09:13, 13.49s/it]

COMMENT: All the Sudan is with Algeria against the pavilion.
OUTPUT: 

{
  "isPolarized": true,
  "political": true,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'isPolarized': True, 'political': True, 'racial_ethnic': True, 'religious': False, 'gender_sexual': False, 'other': False}
COMMENT: The Tunisian Football University has decided to suspend the President of the Regional Association of Manster.
OUTPUT: 

{
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'isPolarized': False, 'political': False, 'racial_ethnic': False, 'religious': False, 'gender_sexual': False, 'other': False}
COMMENT: Congratulations, you're on the clean-up network in the world... the Egyptian mobile phone networks... they're all proudly decent.
OUTPUT: 

{
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": fals

...

COMMENT: It's a disgusting ad. The woman the author shot, and the guy with the fucking mouth, it's a piece of junk in the ad.
OUTPUT: 

{
  "isPolarized": true,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": true,
  "other": false
}
POST-PROCESS: {'isPolarized': True, 'political': False, 'racial_ethnic': False, 'religious': False, 'gender_sexual': True, 'other': False}
COMMENT: I think it's the Hunan accent that doesn't make it to Fujian.
OUTPUT: 

{
  "isPolarized": false,
  "political": false,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'isPolarized': False, 'political': False, 'racial_ethnic': False, 'religious': False, 'gender_sexual': False, 'other': False}
COMMENT: You should think of Zhao Min's personality as Dong Myeong Ju. Do you think Dong Myeong Joo, even if she likes someone, would be a shame to the public?
OUTPUT: 

{
  "isPolarized": true,
  "political": false,
  "raci

 98%|█████████▊| 53/54 [11:30<00:12, 12.99s/it]

COMMENT: As for Gotham's Tiger Girl, she's also black, but she's got an online face.
OUTPUT: 

{
  "isPolarized": true,
  "political": false,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": true,
  "other": false
}
POST-PROCESS: {'isPolarized': True, 'political': False, 'racial_ethnic': True, 'religious': False, 'gender_sexual': True, 'other': False}
COMMENT: I've been to almost every province in the South, and I've been in every province for two or three months on average.
OUTPUT: 

{
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'isPolarized': False, 'political': False, 'racial_ethnic': False, 'religious': False, 'gender_sexual': False, 'other': False}
COMMENT: It's all evidence of the Black River South, isn't it? It's just a bunch of comments.
OUTPUT: 

{
  "isPolarized": true,
  "political": false,
  "racial_ethnic": true,
  "religious": false,
  "gender_sex

100%|██████████| 54/54 [11:39<00:00, 12.96s/it]

COMMENT: I was in a car this morning, and I saw a big man with a little hair and a big waist and a 3-4-year-old daughter.
OUTPUT: 

{
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": true,
  "other": false
}
POST-PROCESS: {'isPolarized': False, 'political': False, 'racial_ethnic': False, 'religious': False, 'gender_sexual': False, 'other': False}
COMMENT: On one occasion, after studying late, he went back to his dormitory, where he saw a pair of eyes coming up and looking closer, and was a black student.
OUTPUT: 

{
  "isPolarized": true,
  "political": false,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'isPolarized': True, 'political': False, 'racial_ethnic': True, 'religious': False, 'gender_sexual': False, 'other': False}
COMMENT: Who are you scolding by comparing this paparazzi to those oppressed women?
OUTPUT: 

{
  "isPolarized": true,
  "political": fals

In [15]:
print(results)

{'arb': {'political': {'TP': 55, 'FP': 71, 'TN': 193, 'FN': 19}, 'racial_ethnic': {'TP': 39, 'FP': 79, 'TN': 206, 'FN': 14}, 'religious': {'TP': 19, 'FP': 69, 'TN': 246, 'FN': 4}, 'gender_sexual': {'TP': 24, 'FP': 37, 'TN': 260, 'FN': 17}, 'other': {'TP': 6, 'FP': 7, 'TN': 273, 'FN': 52}, 'isPolarized': {'TP': 136, 'FP': 100, 'TN': 92, 'FN': 10}, 'not_valid': 0}, 'ben': {'political': {'TP': 84, 'FP': 93, 'TN': 126, 'FN': 30}, 'racial_ethnic': {'TP': 2, 'FP': 145, 'TN': 185, 'FN': 1}, 'religious': {'TP': 3, 'FP': 84, 'TN': 245, 'FN': 1}, 'gender_sexual': {'TP': 1, 'FP': 22, 'TN': 308, 'FN': 2}, 'other': {'TP': 1, 'FP': 5, 'TN': 298, 'FN': 29}, 'isPolarized': {'TP': 129, 'FP': 132, 'TN': 61, 'FN': 11}, 'not_valid': 0}, 'deu': {'political': {'TP': 102, 'FP': 87, 'TN': 101, 'FN': 28}, 'racial_ethnic': {'TP': 47, 'FP': 63, 'TN': 194, 'FN': 14}, 'religious': {'TP': 29, 'FP': 29, 'TN': 250, 'FN': 10}, 'gender_sexual': {'TP': 11, 'FP': 18, 'TN': 284, 'FN': 5}, 'other': {'TP': 3, 'FP': 7, 'TN':

**Statistics**

In [16]:
def compute_statistics(results):
    statistics = {}
    """
    {
        language: {
            overall_macro_F1_categories:
            macro_F1_isPolarized:
        }
    }
    """
    categories_labels = ["political","racial_ethnic","religious","gender_sexual","other"]

    for language, _ in results.items():
        statistics[language] = {}

        TP = results[language]["isPolarized"]["TP"]
        FP = results[language]["isPolarized"]["FP"]
        TN = results[language]["isPolarized"]["TN"]
        FN = results[language]["isPolarized"]["FN"]

        macro_F1_isPolarized = calculate_macro_f1(TP, FP, TN, FN)
        accuracy_isPolarized = accuracy(TP, FP, TN, FN)

        macro_F1_categories = 0
        total_accuracy = 0

        for label in categories_labels:
            TP = results[language][label]["TP"]
            FP = results[language][label]["FP"]
            TN = results[language][label]["TN"]
            FN = results[language][label]["FN"]

            F1 = calculate_macro_f1(TP, FP, TN, FN)
            macro_F1_categories += F1

            total_accuracy += accuracy(TP, FP, TN, FN)

        macro_F1_categories = macro_F1_categories / len(categories_labels)
        accuracy_categories = total_accuracy / len(categories_labels)

        statistics[language]["macro_F1_categories"] = macro_F1_categories
        statistics[language]["macro_F1_isPolarized"] = macro_F1_isPolarized

        statistics[language]["accuracy_categories"] = accuracy_categories
        statistics[language]["accuracy_isPolarized"] = accuracy_isPolarized

    return statistics


In [17]:
statistics = compute_statistics(results)
for language, _ in statistics.items():
    print(f"Stats on language: {language}:")
    print(f"TASK 1 -> Macro F1: {statistics[language]["macro_F1_isPolarized"]} | Accuracy: {statistics[language]["accuracy_isPolarized"]}")
    print(f"TASK 2 ->  Macro F1: {statistics[language]["macro_F1_categories"]} | Accuracy: {statistics[language]["accuracy_categories"]}")
    print(f"Not valid outputs: {results[language]["not_valid"]}")

Stats on language: arb:
TASK 1 -> Macro F1: 0.6689461124764042 | Accuracy: 0.6745562130177515
TASK 2 ->  Macro F1: 0.6294050110894711 | Accuracy: 0.7816568047337278
Not valid outputs: 0
Stats on language: ben:
TASK 1 -> Macro F1: 0.5518844398437868 | Accuracy: 0.5705705705705706
TASK 2 ->  Macro F1: 0.49521588753493473 | Accuracy: 0.7525525525525525
Not valid outputs: 0
Stats on language: deu:
TASK 1 -> Macro F1: 0.6182472989195679 | Accuracy: 0.6383647798742138
TASK 2 ->  Macro F1: 0.6723910274184794 | Accuracy: 0.8182389937106919
Not valid outputs: 0
Stats on language: eng:
TASK 1 -> Macro F1: 0.46228413163897036 | Accuracy: 0.4906832298136646
TASK 2 ->  Macro F1: 0.5503775042870249 | Accuracy: 0.8124223602484472
Not valid outputs: 0
Stats on language: hin:
TASK 1 -> Macro F1: 0.6281928480204343 | Accuracy: 0.7518248175182481
TASK 2 ->  Macro F1: 0.5722906329675557 | Accuracy: 0.7335766423357664
Not valid outputs: 0
Stats on language: ita:
TASK 1 -> Macro F1: 0.3283393375011289 | Acc

In [18]:
results = evaluateClassification(model, sampled_eval_dataset, activeReasoning=True, activeFewShot=True)

Processing arb...


  2%|▏         | 1/43 [00:28<20:10, 28.83s/it]

COMMENT: You threw me in the beginning, and you sneak away your reward, and less than yours, show your black history, and then talk about terror, mind and source of terror.
OUTPUT: 

{
  "rationale": "The comment expresses a mix of accusations and references to historical and contemporary issues, with a derogatory tone toward a racial/ethnic group ('black') and a mention of 'terror', which can be interpreted as targeting a group or identity category.",
  "isPolarized": true,
  "political": true,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'rationale': "The comment expresses a mix of accusations and references to historical and contemporary issues, with a derogatory tone toward a racial/ethnic group ('black') and a mention of 'terror', which can be interpreted as targeting a group or identity category.", 'isPolarized': True, 'political': True, 'racial_ethnic': True, 'religious': False, 'gender_sexual': False, 'other': False}

  5%|▍         | 2/43 [00:55<18:43, 27.40s/it]

COMMENT: All the Sudan is with Algeria against the pavilion.
OUTPUT: 

{
  "rationale": "The comment expresses solidarity between two national groups ('Sudan' and 'Algeria') and does not contain language that targets or insults any group or identity category.",
  "isPolarized": false,
  "political": true,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'rationale': "The comment expresses solidarity between two national groups ('Sudan' and 'Algeria') and does not contain language that targets or insults any group or identity category.", 'isPolarized': False, 'political': False, 'racial_ethnic': False, 'religious': False, 'gender_sexual': False, 'other': False}
COMMENT: The Tunisian Football University has decided to suspend the President of the Regional Association of Manster.
OUTPUT: 

{
  "rationale": "The comment discusses a specific event in the context of sports, without expressing hostility or derogatory attitudes toward a

...

COMMENT: It's a disgusting ad. The woman the author shot, and the guy with the fucking mouth, it's a piece of junk in the ad.
OUTPUT: 

{
  "rationale": "The comment expresses strong negative emotions toward the content of an ad, using derogatory language to describe individuals featured in it.",
  "isPolarized": true,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": true,
  "other": false
}
POST-PROCESS: {'rationale': 'The comment expresses strong negative emotions toward the content of an ad, using derogatory language to describe individuals featured in it.', 'isPolarized': True, 'political': False, 'racial_ethnic': False, 'religious': False, 'gender_sexual': True, 'other': False}
COMMENT: I think it's the Hunan accent that doesn't make it to Fujian.
OUTPUT: 

{
  "rationale": "The comment discusses regional accents without expressing hostility toward any group or identity category.",
  "isPolarized": false,
  "political": false,
  "racial_ethn

 98%|█████████▊| 53/54 [22:14<00:24, 24.83s/it]

COMMENT: As for Gotham's Tiger Girl, she's also black, but she's got an online face.
OUTPUT: 

{
  "rationale": "The comment mentions a racial/ethnic characteristic ('black') but does so in a neutral, descriptive manner, without expressing hostility or derogatory attitudes toward the group.",
  "isPolarized": false,
  "political": false,
  "racial_ethnic": true,
  "religious": false,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'rationale': "The comment mentions a racial/ethnic characteristic ('black') but does so in a neutral, descriptive manner, without expressing hostility or derogatory attitudes toward the group.", 'isPolarized': False, 'political': False, 'racial_ethnic': False, 'religious': False, 'gender_sexual': False, 'other': False}
COMMENT: I've been to almost every province in the South, and I've been in every province for two or three months on average.
OUTPUT: 

{
  "rationale": "The comment discusses travel experiences without expressing any hostility or d

100%|██████████| 54/54 [22:32<00:00, 25.05s/it]

COMMENT: I was in a car this morning, and I saw a big man with a little hair and a big waist and a 3-4-year-old daughter.
OUTPUT: 

{
  "rationale": "The comment describes a person in a neutral manner, focusing on physical characteristics, without expressing hostility or derogatory attitudes toward any group or identity category.",
  "isPolarized": false,
  "political": false,
  "racial_ethnic": false,
  "religious": false,
  "gender_sexual": false,
  "other": false
}
POST-PROCESS: {'rationale': 'The comment describes a person in a neutral manner, focusing on physical characteristics, without expressing hostility or derogatory attitudes toward any group or identity category.', 'isPolarized': False, 'political': False, 'racial_ethnic': False, 'religious': False, 'gender_sexual': False, 'other': False}
COMMENT: On one occasion, after studying late, he went back to his dormitory, where he saw a pair of eyes coming up and looking closer, and was a black student.
OUTPUT: 

{
  "rationale": 

In [19]:
print(results)

{'arb': {'political': {'TP': 46, 'FP': 25, 'TN': 239, 'FN': 28}, 'racial_ethnic': {'TP': 27, 'FP': 33, 'TN': 252, 'FN': 26}, 'religious': {'TP': 16, 'FP': 33, 'TN': 282, 'FN': 7}, 'gender_sexual': {'TP': 22, 'FP': 24, 'TN': 273, 'FN': 19}, 'other': {'TP': 13, 'FP': 18, 'TN': 262, 'FN': 45}, 'isPolarized': {'TP': 118, 'FP': 57, 'TN': 135, 'FN': 28}, 'not_valid': 0}, 'ben': {'political': {'TP': 72, 'FP': 48, 'TN': 171, 'FN': 42}, 'racial_ethnic': {'TP': 1, 'FP': 48, 'TN': 282, 'FN': 2}, 'religious': {'TP': 3, 'FP': 32, 'TN': 297, 'FN': 1}, 'gender_sexual': {'TP': 1, 'FP': 12, 'TN': 318, 'FN': 2}, 'other': {'TP': 6, 'FP': 24, 'TN': 279, 'FN': 24}, 'isPolarized': {'TP': 113, 'FP': 67, 'TN': 126, 'FN': 27}, 'not_valid': 0}, 'deu': {'political': {'TP': 79, 'FP': 49, 'TN': 139, 'FN': 50}, 'racial_ethnic': {'TP': 31, 'FP': 25, 'TN': 231, 'FN': 30}, 'religious': {'TP': 20, 'FP': 15, 'TN': 263, 'FN': 19}, 'gender_sexual': {'TP': 13, 'FP': 14, 'TN': 287, 'FN': 3}, 'other': {'TP': 4, 'FP': 7, 'TN'

In [20]:
statistics = compute_statistics(results)
for language, _ in statistics.items():
    print(f"Stats on language: {language}:")
    print(f"TASK 1 -> Macro F1: {statistics[language]["macro_F1_isPolarized"]} | Accuracy: {statistics[language]["accuracy_isPolarized"]}")
    print(f"TASK 2 ->  Macro F1: {statistics[language]["macro_F1_categories"]} | Accuracy: {statistics[language]["accuracy_categories"]}")
    print(f"Not valid outputs: {results[language]["not_valid"]}")

Stats on language: arb:
TASK 1 -> Macro F1: 0.747882936246764 | Accuracy: 0.7485207100591716
TASK 2 ->  Macro F1: 0.6903522211705398 | Accuracy: 0.8473372781065087
Not valid outputs: 0
Stats on language: ben:
TASK 1 -> Macro F1: 0.7172868497109826 | Accuracy: 0.7177177177177178
TASK 2 ->  Macro F1: 0.5689547788325364 | Accuracy: 0.8588588588588589
Not valid outputs: 0
Stats on language: deu:
TASK 1 -> Macro F1: 0.7127508090614887 | Accuracy: 0.7129337539432177
TASK 2 ->  Macro F1: 0.6964474444159163 | Accuracy: 0.8492113564668771
Not valid outputs: 1
Stats on language: eng:
TASK 1 -> Macro F1: 0.708029478720531 | Accuracy: 0.7080745341614907
TASK 2 ->  Macro F1: 0.6255274000353344 | Accuracy: 0.8788819875776397
Not valid outputs: 0
Stats on language: hin:
TASK 1 -> Macro F1: 0.5938227963575349 | Accuracy: 0.6678832116788321
TASK 2 ->  Macro F1: 0.5594283829838369 | Accuracy: 0.7335766423357665
Not valid outputs: 0
Stats on language: ita:
TASK 1 -> Macro F1: 0.38767605633802815 | Accura